<span id="measure-qubits" />

# Medir qubits



<details>
  <summary><b>Versiones del paquete</b></summary>

  El código de esta página se ha desarrollado teniendo en cuenta los siguientes requisitos.
  Recomendamos utilizar estas versiones o versiones más recientes.

  ```
  qiskit[all]~=2.1.1
  ```
</details>



Para obtener información sobre el estado de un qubit, se puede *medir* en un [bit clásico](/docs/api/qiskit/circuit#qiskit.circuit.Clbit). En Qiskit, las mediciones se realizan en la base computacional, es decir, la base Pauli- $Z$ de un solo qubit. Por lo tanto, una medición da 0 o 1, dependiendo del solapamiento con los estados propios de Pauli- $Z$ $|0\rangle$ y $|1\rangle$ :

$$
|q\rangle \xrightarrow{measure}\begin{cases}
      0 (\text{outcome}+1), \text{with probability } p_0=|\langle q|0\rangle|^{2}\text{,} \\
      1 (\text{outcome}-1), \text{with probability } p_1=|\langle q|1\rangle|^{2}\text{.}
    \end{cases}
$$

<span id="mid-circuit-measurements" />

## Mediciones a mitad de circuito

Las mediciones a mitad de circuito son un componente clave de los circuitos dinámicos. Antes de `qiskit-ibm-runtime` v0.43.0, `measure` era la única instrucción de medida en Qiskit. Sin embargo, las mediciones a mitad de circuito tienen unos requisitos de sintonización diferentes a las mediciones *en los terminales* (mediciones que tienen lugar al final de un circuito). Por ejemplo, hay que tener en cuenta la duración de las instrucciones cuando se ajusta una medición a mitad de circuito, ya que las instrucciones más largas provocan circuitos más ruidosos. No es necesario tener en cuenta la duración de la instrucción para las mediciones terminales porque no hay instrucciones después de las mediciones terminales.

En `qiskit-ibm-runtime` v0.43.0, se introdujo la instrucción `MidCircuitMeasure` . Como su nombre indica, se trata de una nueva instrucción de medición optimizada para la mitad del circuito en las QPU de IBM®.

<Admonition type="note">
  La instrucción `MidCircuitMeasure` se asigna a la instrucción `measure_2` indicada en el backend `supported_instructions`. Sin embargo, `measure_2` no es compatible con todos los backends. Utiliza `service.backends(filters=lambda b: "measure_2" in b.supported_instructions)` para encontrar backends que lo soporten.  Es posible que en el futuro se añadan nuevas medidas, pero no está garantizado.
</Admonition>

<span id="apply-a-measurement-to-a-circuit" />

## Aplicar una medida a un circuito

Hay varias formas de aplicar medidas a un circuito:

<span id="quantumcircuitmeasure-method" />

### `QuantumCircuit.measure` method

Utilice el [`measure`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#measure) método para medir un [`QuantumCircuit`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#quantumcircuit-class).

Ejemplos:



In [1]:
from qiskit import QuantumCircuit

qc = QuantumCircuit(5, 5)
qc.x(0)
qc.x(1)
qc.x(4)
qc.measure(
    range(5), range(5)
)  #  Measures all qubits into the corresponding clbit.

In [2]:
from qiskit import QuantumCircuit

qc = QuantumCircuit(3, 1)
qc.x([0, 2])
qc.measure(1, 0)  # Measure qubit 1 into the classical bit 0.

<span id="measure-class" />

### Clase \`Measure

La clase Qiskit [Measure](/docs/api/qiskit/circuit#qiskit.circuit.Measure) mide los qubits especificados.



In [3]:
from qiskit.circuit import Measure

qc = QuantumCircuit(3, 1)
qc.x([0, 1])
qc.append(Measure(), [0], [0])  # measure qubit 0 into clbit 0

<span id="quantumcircuitmeasure_all-method" />

### `QuantumCircuit.measure_all` method

Para medir todos los qubits en los bits clásicos correspondientes, utilice el método [`measure_all`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#measure_all) método. Por defecto, este método añade nuevos bits clásicos en un `ClassicalRegister` para almacenar estas mediciones.



In [4]:
from qiskit import QuantumCircuit

qc = QuantumCircuit(3, 1)
qc.x([0, 2])
qc.measure_all()  # Measure all qubits.

<span id="quantumcircuitmeasure_active-method" />

### `QuantumCircuit.measure_active` method

Para medir todos los qubits que no están inactivos, utilice el método [`measure_active`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#measure_active) método. Este método crea un nuevo `ClassicalRegister` con un tamaño igual al número de qubits no ociosos que se están midiendo.



In [5]:
from qiskit import QuantumCircuit

qc = QuantumCircuit(3, 1)
qc.x([0, 2])
qc.measure_active()  # Measure qubits that are not idle, that is, qubits 0 and 2.

<span id="midcircuit" />

<span id="midcircuitmeasure-method" />

### `MidCircuitMeasure` método

Utilice `MidCircuitMeasure` para aplicar una medición a mitad de circuito (requiere `qiskit-ibm-runtime` v0.43.0 o posterior).  Aunque puede utilizar `QuantumCircuit.measure` para una medición a mitad de circuito, debido a su diseño, `MidCircuitMeasure` suele ser una mejor opción.  Por ejemplo, añade menos sobrecarga a tu circuito que cuando utilizas `QuantumCircuit.measure`.



In [6]:
from qiskit import QuantumCircuit
from qiskit_ibm_runtime import QiskitRuntimeService
from qiskit_ibm_runtime.circuit import MidCircuitMeasure
from qiskit.circuit import Measure

service = QiskitRuntimeService()
backend = service.least_busy(operational=True, simulator=False)

circ = QuantumCircuit(2, 2)
circ.x(0)
circ.append(MidCircuitMeasure(), [0], [0])
# circ.measure([0], [0])
# circ.measure_all()
print(circ.draw(cregbundle=False))

     ┌───┐┌────────────┐
q_0: ┤ X ├┤0           ├
     └───┘│            │
q_1: ─────┤  Measure_2 ├
          │            │
c_0: ═════╡0           ╞
          └────────────┘
c_1: ═══════════════════
                        


<Admonition type="attention" title="Notas importantes">
  *   Debe haber al menos un registro clásico para poder utilizar mediciones.
  *   La primitiva Sampler requiere mediciones del circuito. Puede añadir mediciones de circuito con la primitiva Estimador, pero se ignoran.
</Admonition>



<span id="next-steps" />

## Pasos siguientes

<Admonition type="tip" title="Recomendaciones">
  *   [`Measure`](/docs/api/qiskit/circuit#qiskit.circuit.Measure) clase
  *   [`measure_all`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#measure_all) método
  *   [`measure_active`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#measure_active) método
  *   [`random_circuit`](/docs/api/qiskit/circuit_random#qiskit.circuit.random.random_circuit) método
</Admonition>



© IBM Corp., 2017-2026